Attempt 010 Summarization - followup of Attempt 008 summarization with 10fold cross-validation

In [ ]:
%env CUDA_VISIBLE_DEVICES=0
!pip install transformers datasets
!pip install cloud-tpu-client==0.10 torch==1.12.0 https://storage.googleapis.com/tpu-pytorch/wheels/colab/torch_xla-1.12-cp37-cp37m-linux_x86_64.whl tensorboard-plugin-profile
!pip install accelerate

env: CUDA_VISIBLE_DEVICES=0
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Using cached https://storage.googleapis.com/tpu-pytorch/wheels/colab/torch_xla-1.12-cp37-cp37m-linux_x86_64.whl (187.4 MB)
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
#adapted from https://github.com/FakeNewsChallenge/fnc-1-baseline/tree/master/utils
from csv import DictReader
import random
import os
from collections import defaultdict
import sys
import os
import re
import argparse

In [ ]:
#Loading dataset from summaries
class DataReaderFromPath():
    def __init__(self, name="train", path="fnc-1", is_unlabeled=False):
        self.path = path
        print("Reading data from path : " + str(path) + " " )
        summaries = name + "_summaries.csv"
        stances = name + "_stances"
        if is_unlabeled is True:
            stances = stances + "_unlabeled"
        stances = stances + ".csv"

        self.stances = self.read(stances)
        articlesSummaries = self.read(summaries)
        self.summaries = dict()

        # make the body ID an integer value
        for s in self.stances:
            s['Body ID'] = int(s['Body ID'])

        # copy all bodies into a dictionary
        for summary in articlesSummaries:
            self.summaries[int(summary['Body ID'])] = summary['articleSummary']

        print("Total stances: " + str(len(self.stances)))
        print("Total summaries: " + str(len(self.summaries)))

    def read(self, filename):
        rows = []
        with open(self.path + "/" + filename, "r", encoding='utf-8') as table:
            r = DictReader(table)

            for line in r:
                rows.append(line)
        return rows

In [ ]:
import random
import os
from collections import defaultdict


def generate_hold_out_split (dataset, training = 0.8, base_dir="splits"):
    r = random.Random()
    r.seed(1489215)

    article_ids = list(dataset.articles.keys())  # get a list of article ids
    r.shuffle(article_ids)  # and shuffle that list


    training_ids = article_ids[:int(training * len(article_ids))]
    hold_out_ids = article_ids[int(training * len(article_ids)):]

    # write the split body ids out to files for future use
    with open(base_dir+ "/"+ "training_ids.txt", "w+") as f:
        f.write("\n".join([str(id) for id in training_ids]))

    with open(base_dir+ "/"+ "hold_out_ids.txt", "w+") as f:
        f.write("\n".join([str(id) for id in hold_out_ids]))


def read_ids(file,base):
    ids = []
    with open(base+"/"+file,"r") as f:
        for line in f:
           ids.append(int(line))
        return ids


def kfold_split(dataset, training = 0.8, n_folds = 10, base_dir="splits"):
    if not (os.path.exists(base_dir+ "/"+ "training_ids.txt")
            and os.path.exists(base_dir+ "/"+ "hold_out_ids.txt")):
        generate_hold_out_split(dataset,training,base_dir)

    training_ids = read_ids("training_ids.txt", base_dir)
    hold_out_ids = read_ids("hold_out_ids.txt", base_dir)

    folds = []
    for k in range(n_folds):
        folds.append(training_ids[int(k*len(training_ids)/n_folds):int((k+1)*len(training_ids)/n_folds)])

    return folds,hold_out_ids


def get_stances_for_folds(dataset,folds,hold_out):
    stances_folds = defaultdict(list)
    stances_hold_out = []
    for stance in dataset.stances:
        if stance['Body ID'] in hold_out:
            stances_hold_out.append(stance)
        else:
            fold_id = 0
            for fold in folds:
                if stance['Body ID'] in fold:
                    stances_folds[fold_id].append(stance)
                fold_id += 1

    return stances_folds,stances_hold_out


Reading data from path : fnc-1 
Total stances: 49972
Total summaries: 1683


In [ ]:
d = DataReaderFromPath()

In [ ]:
# Adapted from https://github.com/FakeNewsChallenge/fnc-1/blob/master/scorer.py
from sklearn.metrics import confusion_matrix
from sklearn.metrics import precision_recall_fscore_support, accuracy_score
import json
LABELS = ['agree', 'disagree', 'discuss', 'unrelated']
LABELS_RELATED = ['unrelated', 'related']
RELATED = LABELS[0:3]


def score_submission(gold_labels, test_labels):
    score = 0.0
    cm = [[0, 0, 0, 0],
          [0, 0, 0, 0],
          [0, 0, 0, 0],
          [0, 0, 0, 0]]

    for i, (g, t) in enumerate(zip(gold_labels, test_labels)):
        g_stance, t_stance = g, t
        if g_stance == t_stance:
            score += 0.25
            if g_stance != 'unrelated':
                score += 0.50
        if g_stance in RELATED and t_stance in RELATED:
            score += 0.25

        cm[LABELS.index(g_stance)][LABELS.index(t_stance)] += 1

    return score, cm


def print_confusion_matrix(cm):
    lines = []
    header = "|{:^11}|{:^11}|{:^11}|{:^11}|{:^11}|".format('', *LABELS)
    line_len = len(header)
    lines.append("-" * line_len)
    lines.append(header)
    lines.append("-" * line_len)

    hit = 0
    total = 0
    for i, row in enumerate(cm):
        hit += row[i]
        total += sum(row)
        lines.append("|{:^11}|{:^11}|{:^11}|{:^11}|{:^11}|".format(LABELS[i],
                                                                   *row))
        lines.append("-" * line_len)
    print('\n'.join(lines))


def report_score(actual, predicted):
    score, cm = score_submission(actual, predicted)
    best_score, _ = score_submission(actual, actual)

    print_confusion_matrix(cm)
    print("Score: " + str(score) + " out of " + str(best_score) + "\t(" + str(score * 100 / best_score) + "%)")
    all_values = get_precision_recall_f1_scores(actual, predicted)

    print("--All Metrics --")
    print(json.dumps(all_values, indent=4, sort_keys=True, separators=(',', ': ')))

    return score * 100 / best_score

#Calculating accuracy precision recall f1 scores
def get_precision_recall_f1_scores(actual, predicted):
    # calculate precision scores for labels - Average None
    p, r, f1, _ = precision_recall_fscore_support(y_true=actual, y_pred=predicted, labels=LABELS, zero_division=0.0,
                                                  average=None)

    precisions = [{LABELS[index] : value} for (index, value) in enumerate(p)]
    recalls = [{LABELS[index] : value} for (index, value) in enumerate(r)]
    f1_scores = [{LABELS[index] : value} for (index, value) in enumerate(f1)]
    acc = accuracy_score(actual, predicted)
    avg_none = {"accuracy": acc, "precision": precisions, "recall": recalls, "f1": f1_scores}

    # calculate precision scores for labels - Average micro
    p, r, f1, _ = precision_recall_fscore_support(y_true=actual, y_pred=predicted, labels=LABELS, zero_division=0.0,
                                                  average='micro')

    avg_micro = {"accuracy": acc, "precision": p, "recall": r, "f1": f1}

    # calculate precision scores for labels - Average macro
    p, r, f1, _ = precision_recall_fscore_support(y_true=actual, y_pred=predicted, labels=LABELS, zero_division=0.0,
                                                  average='macro')

    avg_macro = {"accuracy": acc, "precision": p, "recall": r, "f1": f1}

    # calculate precision scores for labels - Average weighted
    p, r, f1, _ = precision_recall_fscore_support(y_true=actual, y_pred=predicted, labels=LABELS, zero_division=0.0,
                                                  average='weighted')

    avg_weighted = {"accuracy": acc, "precision": p, "recall": r, "f1": f1}

    all_values = {"Each_Class": avg_none, "micro": avg_micro, "macro": avg_macro, "weighted": avg_weighted}

    return all_values

def compute_metrics(pred):
    actual = [LABELS[int(a)] for a in pred.label_ids]#pred.label_ids
    predicted = [LABELS[int(a)] for a in pred.predictions.argmax(-1)]#pred.predictions.argmax(-1)
    acc = accuracy_score(actual, predicted)
    # calculate precision scores for labels - Average macro
    p, r, f1, _ = precision_recall_fscore_support(y_true=actual, y_pred=predicted, labels=LABELS, zero_division=0.0,
                                                  average='macro')

    avg_macro = {"accuracy": acc, "precision": p, "recall": r, "f1": f1}

    return avg_macro

In [ ]:
#adapted from https://github.com/FakeNewsChallenge/fnc-1-baseline/blob/master/feature_engineering.py
import os
import re
import nltk
import numpy as np
from tqdm import tqdm

def combine_headline_and_bodies(headlines, bodies):
    X = []
    for i, (headline, body) in tqdm(enumerate(zip(headlines, bodies))):
        joinedStr = headline + " <TitleSummarySep> " + body
        X.append(joinedStr)
    return X

2it [00:00, 24244.53it/s]

['The world is ending <TitleSummarySep> The world is ending', 'We all are about to die <TitleSummarySep> We all are about to die. Everyone will be dead. We will. Kill us.']


In [ ]:
headlines = ["The world is ending","We all are about to die"]
bodies = ["The world is ending","We all are about to die. Everyone will be dead. We will. Kill us."]
fp = combine_headline_and_bodies(headlines, bodies)
print(fp)

In [ ]:
#adapted from https://github.com/FakeNewsChallenge/fnc-1-baseline/blob/master/fnc_kfold.py
import sys
import numpy as np


def generate_labeled_data(stances, dataset, name):
    h, b, y = [], [], []

    for stance in stances:
        y.append((LABELS.index(stance['Stance'])))
        h.append(stance['Headline'])
        b.append(dataset.summaries[stance['Body ID']])

    X = combine_headline_and_bodies(h, b)
    print(y)

    return X, y


def generate_data_without_labels(stances, dataset, name):
    h, b= [], []

    for stance in stances:
        h.append(stance['Headline'])
        b.append(dataset.summaries[stance['Body ID']])
        
    X = combine_headline_and_bodies(h, b)
    return X

Reading data from path : fnc-1 
Total stances: 49972
Total summaries: 1683


9622it [00:00, 797155.53it/s]


[3, 0, 3, 3, 0, 3, 3, 3, 3, 3, 3, 0, 3, 3, 3, 0, 3, 3, 3, 3, 3, 3, 3, 0, 3, 3, 0, 3, 3, 0, 3, 3, 3, 3, 2, 3, 3, 3, 3, 3, 3, 2, 3, 3, 3, 0, 3, 3, 3, 3, 3, 3, 2, 3, 3, 3, 3, 3, 3, 3, 3, 2, 3, 3, 0, 2, 3, 3, 2, 3, 2, 3, 1, 3, 0, 3, 3, 3, 3, 3, 2, 3, 3, 1, 3, 2, 3, 3, 3, 3, 3, 3, 2, 3, 3, 3, 3, 3, 3, 3, 3, 2, 3, 3, 3, 3, 2, 3, 3, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 2, 2, 3, 3, 3, 3, 3, 3, 0, 2, 3, 3, 2, 3, 2, 3, 3, 3, 0, 0, 3, 3, 3, 3, 3, 3, 0, 2, 3, 3, 3, 3, 2, 3, 3, 3, 3, 3, 3, 3, 2, 3, 3, 2, 3, 3, 3, 2, 0, 3, 3, 2, 3, 3, 3, 3, 0, 3, 3, 3, 3, 3, 3, 3, 3, 0, 3, 3, 0, 3, 3, 3, 2, 3, 0, 2, 3, 3, 2, 3, 3, 3, 2, 3, 3, 3, 2, 3, 3, 3, 3, 3, 2, 3, 3, 2, 3, 0, 0, 2, 3, 3, 2, 0, 3, 2, 3, 3, 3, 3, 3, 3, 3, 0, 3, 3, 3, 3, 2, 3, 3, 2, 3, 3, 3, 3, 3, 3, 3, 3, 0, 3, 3, 3, 3, 3, 3, 3, 2, 3, 3, 0, 3, 3, 3, 3, 3, 3, 3, 0, 3, 2, 3, 3, 3, 0, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 0, 3, 3, 2, 2, 3, 2, 2, 3, 3, 3, 3, 3, 2, 3, 3, 3, 2, 3, 2, 0, 3, 3, 3, 3, 3, 1, 3, 3, 2, 3, 2, 3, 3, 3, 3, 3, 3, 

4124it [00:00, 580602.50it/s]


[0, 3, 3, 0, 3, 3, 2, 3, 3, 0, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 0, 3, 3, 3, 3, 3, 3, 3, 3, 1, 3, 3, 2, 3, 3, 3, 2, 1, 3, 0, 3, 3, 3, 3, 3, 3, 3, 3, 1, 3, 0, 3, 0, 3, 3, 2, 3, 2, 3, 3, 3, 3, 3, 2, 3, 3, 3, 3, 3, 2, 3, 3, 2, 0, 0, 0, 3, 3, 3, 3, 0, 3, 0, 3, 3, 3, 3, 3, 3, 3, 2, 3, 3, 0, 3, 3, 1, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 2, 2, 0, 3, 3, 3, 3, 2, 2, 3, 3, 3, 3, 3, 3, 2, 1, 3, 3, 3, 3, 3, 3, 3, 3, 2, 3, 3, 3, 3, 1, 3, 3, 1, 3, 3, 0, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 0, 3, 3, 3, 3, 0, 3, 0, 3, 3, 2, 0, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 0, 3, 3, 3, 2, 3, 3, 3, 3, 2, 3, 3, 3, 3, 2, 0, 1, 3, 3, 3, 2, 3, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 2, 2, 3, 3, 3, 3, 3, 3, 3, 2, 0, 3, 3, 3, 3, 3, 3, 2, 3, 3, 0, 2, 3, 3, 3, 3, 3, 2, 2, 3, 3, 2, 3, 3, 0, 3, 3, 3, 3, 3, 2, 2, 2, 3, 0, 2, 0, 3, 2, 3, 3, 3, 3, 2, 3, 0, 3, 2, 3, 3, 0, 3, 3, 3, 3, 3, 3, 3, 3, 3, 0, 3, 3, 3, 0, 3, 3, 0, 2, 3, 3, 3, 1, 3, 3, 3, 2, 3, 3, 3, 3, 2, 2, 3, 2, 3, 3, 1, 0, 3, 3, 

...

[2, 0, 2, 0, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 0, 3, 2, 3, 1, 3, 3, 0, 0, 2, 3, 3, 2, 2, 3, 3, 3, 3, 3, 0, 2, 3, 3, 3, 3, 3, 3, 2, 3, 3, 2, 1, 3, 2, 3, 3, 0, 2, 3, 3, 3, 3, 3, 0, 3, 3, 3, 3, 3, 3, 3, 3, 3, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 2, 0, 3, 3, 3, 3, 3, 3, 2, 3, 3, 3, 3, 3, 2, 3, 3, 3, 0, 3, 3, 3, 2, 3, 3, 3, 3, 2, 3, 2, 2, 3, 1, 3, 2, 3, 0, 3, 3, 3, 2, 3, 3, 3, 3, 3, 3, 3, 0, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 0, 3, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 2, 3, 3, 3, 1, 3, 3, 2, 3, 3, 3, 3, 3, 0, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 1, 3, 3, 3, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 1, 3, 3, 3, 3, 3, 3, 0, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 2, 3, 3, 3, 3, 3, 3, 0, 3, 2, 3, 3, 3, 3, 3, 3, 3, 3, 2, 3, 3, 2, 3, 3, 3, 3, 2, 3, 3, 3, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 0, 0, 3, 2, 3, 3, 3, 3, 0, 2, 1, 3, 3, 3, 2, 3, 3, 2, 0, 3, 3, 3, 3, 3, 3, 3, 3, 2, 3, 2, 3, 3, 3, 3, 3, 2, 2, 3, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 2, 3, 3, 3, 3, 3, 2, 3, 3, 3, 3, 2, 3, 0, 3, 0, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 2, 3, 3, 

4039it [00:00, 817487.52it/s]


[2, 3, 3, 1, 3, 3, 3, 3, 3, 3, 0, 3, 3, 3, 3, 2, 3, 0, 3, 3, 0, 3, 3, 3, 3, 3, 2, 3, 3, 3, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 0, 0, 3, 3, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 2, 3, 2, 3, 3, 2, 2, 3, 2, 3, 3, 0, 3, 0, 0, 3, 3, 2, 3, 3, 3, 3, 2, 0, 3, 3, 0, 3, 3, 2, 3, 3, 2, 0, 2, 3, 3, 3, 3, 2, 0, 3, 0, 3, 3, 3, 3, 1, 3, 1, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 2, 3, 3, 3, 3, 3, 3, 3, 1, 3, 0, 3, 3, 3, 3, 3, 0, 3, 3, 3, 3, 3, 3, 3, 3, 2, 3, 3, 3, 3, 3, 2, 2, 3, 3, 3, 3, 3, 0, 2, 3, 3, 3, 2, 3, 3, 3, 3, 3, 3, 2, 3, 2, 3, 3, 2, 0, 2, 2, 3, 3, 3, 3, 1, 3, 0, 3, 3, 3, 3, 3, 2, 2, 0, 3, 3, 3, 3, 2, 3, 3, 3, 3, 3, 3, 3, 3, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 2, 3, 3, 3, 3, 3, 3, 2, 0, 3, 0, 3, 3, 3, 2, 3, 3, 3, 3, 3, 0, 0, 3, 2, 3, 3, 3, 2, 3, 3, 3, 3, 3, 3, 3, 2, 3, 2, 3, 3, 3, 3, 3, 3, 3, 2, 3, 2, 3, 3, 3, 3, 3, 1, 3, 2, 3, 3, 3, 2, 2, 0, 3, 3, 3, 2, 3, 3, 0, 2, 2, 3, 3, 3, 3, 3, 3, 3, 2, 3, 2, 2, 3, 0, 3, 2, 2, 3, 3, 3, 3, 2, 2, 2, 2, 0, 3, 2, 3, 1, 3, 3, 3, 3, 3, 3, 3, 3, 2, 3, 3, 3, 2, 

3944it [00:00, 854238.83it/s]


[1, 3, 3, 2, 3, 3, 3, 3, 3, 3, 3, 1, 3, 3, 3, 2, 3, 3, 2, 2, 2, 2, 2, 3, 2, 3, 3, 3, 3, 3, 0, 3, 3, 3, 3, 0, 3, 2, 3, 2, 3, 2, 3, 2, 3, 0, 3, 3, 3, 3, 3, 3, 2, 3, 2, 2, 2, 3, 0, 3, 0, 3, 3, 3, 3, 3, 3, 3, 0, 3, 2, 3, 3, 0, 2, 3, 3, 3, 2, 3, 2, 3, 2, 0, 3, 3, 3, 3, 3, 3, 0, 0, 3, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 0, 3, 3, 3, 3, 0, 3, 3, 3, 3, 3, 3, 0, 0, 3, 3, 0, 3, 3, 0, 3, 3, 3, 0, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 0, 3, 3, 3, 0, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 0, 3, 3, 3, 3, 3, 3, 3, 3, 3, 2, 3, 3, 3, 2, 3, 3, 3, 3, 3, 3, 3, 2, 3, 3, 2, 3, 0, 3, 3, 3, 2, 3, 2, 3, 3, 3, 3, 3, 3, 0, 3, 3, 3, 3, 0, 3, 3, 3, 3, 3, 3, 3, 3, 2, 3, 0, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 2, 3, 3, 0, 3, 3, 3, 3, 3, 3, 3, 3, 2, 3, 0, 3, 3, 3, 3, 2, 2, 0, 0, 3, 3, 2, 3, 3, 0, 3, 3, 3, 2, 3, 3, 3, 0, 3, 3, 3, 3, 2, 3, 3, 3, 3, 3, 3, 0, 3, 3, 2, 3, 3, 3, 3, 3, 3, 2, 2, 3, 3, 3, 0, 3, 3, 3, 3, 3, 3, 2, 3, 3, 3, 0, 3, 2, 3, 3, 3, 2, 3, 3, 3, 2, 3, 1, 3, 3, 3, 3, 3, 2, 3, 3, 3, 3, 2, 3, 3, 2, 3, 

In [ ]:
import sys
import numpy as np

from sklearn.ensemble import AdaBoostClassifier
import pandas as pd
from datasets import Dataset, DatasetDict

#check_version()
#parse_params()

# Load the training dataset and generate folds
d = DataReaderFromPath()

Xs = {}
ys = {}
folds, hold_out = kfold_split(d, n_folds=10)
fold_stances, hold_out_stances = get_stances_for_folds(d, folds, hold_out)
# Load/Precompute all features now
X_holdout, y_holdout = generate_labeled_data(hold_out_stances, d, "holdout")
for fold in fold_stances:
    Xs[fold], ys[fold] = generate_labeled_data(fold_stances[fold], d, str(fold))


# Load the competition dataset
unlabeled_competition_dataset = DataReaderFromPath(name="competition_test", is_unlabeled=True)

In [ ]:
unlabeled_competition_dataset

25413it [00:00, 845790.07it/s]


In [ ]:
X_unlabeled = generate_data_without_labels(unlabeled_competition_dataset.stances, unlabeled_competition_dataset,"competition_unlabeled")

25413

In [ ]:
len(X_unlabeled)

In [ ]:
def get_X_data_in_batches(X_data):
  dataset_in_batches = []
  batch_size = 200
  i = 1
  batch = []

  for data in X_data:
    batch.append(data)
    if(i == 200):
      batch_to_append = batch.copy()
      print(batch_to_append[0])
      dataset_in_batches.append(batch_to_append)
      batch.clear()
      i=0

    i = i+1
    #print(i)

  if len(batch) > 0:
    dataset_in_batches.append(batch)
    batch = []

  return dataset_in_batches

In [ ]:
def get_XY_data_in_batches(X_data, y_data):
  dataset_in_batches = []
  batch_size = 200
  i = 1
  batch = []

  for index, xdata in enumerate(X_data):
    data = DatasetDict(
        X = xdata,
        y = y_data[index],
    )
    batch.append(data)
    if(i == 200):
      batch_to_append = batch.copy()
      print(batch_to_append[0])
      dataset_in_batches.append(batch_to_append)
      batch.clear()
      i=0

    i = i+1
    #print(i)

  if len(batch) > 0:
    dataset_in_batches.append(batch)
    batch = []

  return dataset_in_batches

Ferguson riots: Pregnant woman loses eye after cops fire BEAN BAG round through car window <TitleSummarySep> Helric Fredou, 45, turned a gun on himself in his police office in Limoges. A colleague found his body at 1am on Thursday, the day after three gunmen fired at the satirical magazine's office and left 12 people dead. Union of Commissioners of the National Police confirmed Mr Fredou took his own life.
Bear attack foiled by Justin Bieber’s music: A story too good to check <TitleSummarySep> President Cristina Fernandez de Kirchhner adopted Yair Tawil as her godson. Tradition says the seventh son in a family will turn into a werewolf and eat unbaptized babies. Yair is the first Jewish boy to be adopted, as the practice only applied to Catholics until 2009.
Finally, proof that Justin Bieber IS unbearable: Russian fisherman saved from bear attack when ringtone featuring one of the pop brat's songs scares it away <TitleSummarySep> A customer says he was able to change the quality of App

In [ ]:
competition_dataset_in_batches = get_X_data_in_batches(X_unlabeled)

DatasetDict({
    X: Police find mass graves with at least '15 bodies' near Mexico town where 43 students disappeared after police clash <TitleSummarySep> Seth Rogen is being eyed to play Apple co-founder Steve Wozniak in Sony’s Steve Jobs biopic. Danny Boyle is directing the untitled film, based on Walter Isaacson's book and adapted by Aaron Sorkin. Christian Bale, the actor who is to play Jobs, is still in the midst of closing his deal.
    y: 3
})
DatasetDict({
    X: Predator Drone Reportedly Spotted Over ISIS Hotbed in Syria; Airstrikes Hit ISIS Targets <TitleSummarySep> U.S. drones are hunting for al-Baghdadi, according to reports in the Telegraph. Reports say the U.S.-led coalition is using drones to hunt for the ISIS leader. The Telegraph reports that the drones are believed to be armed with machine guns and drones.
    y: 2
})
DatasetDict({
    X: One of 'Taliban Five' in Bowe Bergdahl swap allegedly returned to militancy <TitleSummarySep> The lethal animals are being launched

In [ ]:
holdout_dataset_in_batches = get_XY_data_in_batches(X_holdout,y_holdout)

In [ ]:
competition_data_dict_list = []
for batch in competition_dataset_in_batches:
    data_dict =DatasetDict(
      competition=Dataset.from_dict(
          {
              "text": batch,
              "label": [3]*len(batch),
          }
      )
    )
    competition_data_dict_list.append(data_dict)

In [ ]:
holdout_data_dict_list = []
for batch in holdout_dataset_in_batches:
  #print(batch)
  X_values = []
  y_values = []
  for dict_val in batch:
    X_values.append(dict_val["X"])
    y_values.append(dict_val["y"])
  data_dict =DatasetDict(
    holdout=Dataset.from_dict(
        {
            "text": X_values,
            "label": y_values,
        }
    )
  )
  holdout_data_dict_list.append(data_dict)

'Bear attack foiled by Justin Bieber’s music: A story too good to check <TitleSummarySep> President Cristina Fernandez de Kirchhner adopted Yair Tawil as her godson. Tradition says the seventh son in a family will turn into a werewolf and eat unbaptized babies. Yair is the first Jewish boy to be adopted, as the practice only applied to Catholics until 2009.'

In [ ]:
competition_data_dict_list[1]['competition']['text'][0]

'Predator Drone Reportedly Spotted Over ISIS Hotbed in Syria; Airstrikes Hit ISIS Targets <TitleSummarySep> U.S. drones are hunting for al-Baghdadi, according to reports in the Telegraph. Reports say the U.S.-led coalition is using drones to hunt for the ISIS leader. The Telegraph reports that the drones are believed to be armed with machine guns and drones.'

In [ ]:
holdout_data_dict_list[1]['holdout']['text'][0]

1

In [ ]:
import os, numpy as np

from transformers import (
    AutoTokenizer,
    AutoModelForSequenceClassification,
    TrainingArguments,
    Trainer,
)

#adapted from https://github.com/Demfier/pytorch-tutorials/blob/main/bert_classifier/train.py
tokenizer = AutoTokenizer.from_pretrained("distilbert-base-uncased", use_fast=True)
new_token = "<TitleSummarySep>"
tokenizer.add_tokens(new_token)



In [ ]:
def preprocess(example):
  result =  tokenizer(example["text"], max_length=200, truncation=True, padding='max_length')  
  return result

  0%|          | 0/1 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

...

  0%|          | 0/1 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

In [ ]:
encoded_competitiondataset_list = [competition_data_dict.map(preprocess, batched=True) for competition_data_dict in competition_data_dict_list]

Some weights of the model checkpoint at distilbert-base-uncased were not used when initializing DistilBertForSequenceClassification: ['vocab_transform.bias', 'vocab_projector.bias', 'vocab_transform.weight', 'vocab_layer_norm.weight', 'vocab_layer_norm.bias', 'vocab_projector.weight']
- This IS expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['classifier.weight', 'pre_classifier.weight', 'pre_clas

The following columns in the training set don't have a corresponding argument in `DistilBertForSequenceClassification.forward` and have been ignored: text. If text are not expected by `DistilBertForSequenceClassification.forward`,  you can safely ignore this message.
/usr/local/lib/python3.7/dist-packages/transformers/optimization.py:310: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  FutureWarning,
***** Running training *****
  Num examples = 36226
  Num Epochs = 50
  Instantaneous batch size per device = 128
  Total train batch size (w. parallel, distributed & accumulation) = 1024
  Gradient Accumulation steps = 1
  Total optimization steps = 1800


/usr/local/lib/python3.7/dist-packages/transformers/optimization.py:310: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  FutureWarning,


/usr/local/lib/python3.7/dist-packages/transformers/optimization.py:310: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  FutureWarning,


/usr/local/lib/python3.7/dist-packages/transformers/optimization.py:310: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  FutureWarning,


/usr/local/lib/python3.7/dist-packages/transformers/optimization.py:310: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  FutureWarning,


...

The following columns in the test set don't have a corresponding argument in `DistilBertForSequenceClassification.forward` and have been ignored: text. If text are not expected by `DistilBertForSequenceClassification.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 200
  Batch size = 128


The following columns in the test set don't have a corresponding argument in `DistilBertForSequenceClassification.forward` and have been ignored: text. If text are not expected by `DistilBertForSequenceClassification.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 200
  Batch size = 128


The following columns in the test set don't have a corresponding argument in `DistilBertForSequenceClassification.forward` and have been ignored: text. If text are not expected by `DistilBertForSequenceClassification.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 200
  Batch size = 128


The following columns in the test set don't have a corresponding argument in `DistilBertForSequenceClassification.forward` and have been ignored: text. If text are not expected by `DistilBertForSequenceClassification.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 200
  Batch size = 128


The following columns in the test set don't have a corresponding argument in `DistilBertForSequenceClassification.forward` and have been ignored: text. If text are not expected by `DistilBertForSequenceClassification.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 13
  Batch size = 128


In [ ]:
import itertools
import torch_xla.distributed.xla_multiprocessing as xmp
from pathlib import Path


backbone = AutoModelForSequenceClassification.from_pretrained(
        "distilbert-base-uncased", num_labels=4
    )
backbone.resize_token_embeddings(len(tokenizer))
WRAPPED_MODEL = xmp.MpModelWrapper(backbone)

def train_fnc(WRAPPED_MODEL, device):
  # We wrap this 
  model = WRAPPED_MODEL.to(device)

  # https://huggingface.co/docs/transformers/v4.20.1/en/main_classes/trainer#transformers.TrainingArguments
  training_args = TrainingArguments(
      "checkpoints",
      evaluation_strategy="epoch",
      save_strategy="epoch",
      learning_rate=1e-5,
      warmup_ratio=0.1,
      weight_decay=0.01,
      load_best_model_at_end=True,
      num_train_epochs=50,
      metric_for_best_model="accuracy",
      per_device_eval_batch_size=128,
      per_device_train_batch_size=128,
      tpu_num_cores = 8,
  )

  best_fold = None

  directory_path = Path("nli_model/")
  if not directory_path.exists():
    


    best_score = 0
    # Classifier for each fold
    for fold in fold_stances:

        #Removing the fold from consideration
        ids = list(range(len(folds)))
        del ids[fold]

        #trainingset consists of everything except for the fold
        X_train = list(itertools.chain(*tuple([Xs[i] for i in ids])))
        y_train = list(itertools.chain(*tuple([ys[i] for i in ids])))

        data_dict = DatasetDict(
          train=Dataset.from_dict(
              {
                  "text": X_train, 
                  "label": y_train
              }
          ),
          test=Dataset.from_dict(
              {
                  "text": Xs[fold],
                  "label": ys[fold],
              }
          )
        )

        encoded_dataset = data_dict.map(preprocess, batched=True)

        trainer = Trainer(
            model,
            training_args,
            train_dataset=encoded_dataset["train"],
            eval_dataset=encoded_dataset["test"],
            tokenizer=tokenizer,
            compute_metrics=compute_metrics,
        )

        trainer.place_model_on_device = False
        trainer.train()
        predicted, _, _ = trainer.predict(encoded_dataset["test"])  
        labeled_Predictions = [LABELS[int(a)] for a in np.argmax(predicted, axis=-1)]
        actual = [LABELS[int(a)] for a in encoded_dataset["test"]["label"]]

        fold_score, _ = score_submission(actual, labeled_Predictions)
        max_fold_score, _ = score_submission(actual, actual)

        score = fold_score / max_fold_score

        print("Score for fold " + str(fold) + " was - " + str(score))
        if score > best_score:
            best_score = score
            best_fold = trainer

    #Saving the best fold model
    best_fold.save_model("nli_model/")
    tokenizer.save_pretrained("nli_model/")

  else:
    print("Loading model")
    best_fold = AutoModelForSequenceClassification.from_pretrained("./nli_model/").to(device)

  print(best_fold)

  holdout_data_dict = DatasetDict(
      holdout = Dataset.from_dict(
          {
              "text": X_holdout,
              "label": y_holdout,
          }
      )
    )

  encoded_holdout_dataset_list = [holdout_data_dict.map(preprocess, batched=True) for holdout_data_dict in holdout_data_dict_list]
  #encoded_holdout_dataset = holdout_data_dict.map(preprocess, batched=True)

  labeled_Predictions = []
  actual_predictions = []
  for encoded_holdout_dataset in encoded_holdout_dataset_list:
    prediction, _, _ = best_fold.predict(encoded_holdout_dataset["holdout"])
    labeled_Prediction = [LABELS[int(a)] for a in np.argmax(prediction, axis=-1)]
    labeled_Predictions.extend(labeled_Prediction)

    actual = [LABELS[int(a)] for a in encoded_holdout_dataset["holdout"]["label"]]
    actual_predictions.extend(actual)

  print("Scores on the dev set")
  report_score(actual_predictions, labeled_Predictions)
  print("")
  print("")

  result = []
  i = 0
  for encoded_competition_dataset in encoded_competitiondataset_list:
    predictions, _, _ = trainer.predict(encoded_competition_dataset["competition"])  
    labeled_Predictions = [LABELS[int(a)] for a in np.argmax(predictions, axis=-1)]

    for predictedLabel in labeled_Predictions:
        dict = {
            "Headline": unlabeled_competition_dataset.stances[i]['Headline'],
            "Body ID": unlabeled_competition_dataset.stances[i]['Body ID'],
            "Stance": predictedLabel
        }
        result.append(dict)
        i += 1

  test_data = pd.DataFrame(result)
  test_data.to_csv('answer.csv', index=False, encoding='utf-8')  # From pandas library

  return trainer


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>